<h2 style="text-align: center;">How to reprocess ODFs to generate calibrated and concatenated EPIC event lists </h2>
<br>
<center>
<table border="0" style="background-color: #DDDDDD; width: 100%;">
	<tbody>
		<tr>
			<td style="padding: 2px; text-align: left;">
			<p><b>Introduction</b></p>
			<p style="text-align: justify;">This thread illustrates how to reprocess Observation Data Files (ODFs) to obtain calibrated and concatenated event lists.</p>
			<p><b>Expected Outcome</b></p>
			<p style="text-align: justify;">The user will obtain calibrated and concatenated event lists which can be directly used to generate scientific products (images, spectra, light curves) through the SAS tasks <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/evselect/index.html" target="_parent"><tt>evselect</tt></a> or <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/xmmselect/index.html" target="_parent"><tt>xmmselect</tt></a>.</p>
			<p><b>SAS Tasks to be Used</b></p>
			<ul>
				<li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/emproc/index.html" target="_parent"><tt>emproc</tt></a></li>
				<li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epproc/index.html" target="_parent"><tt>epproc</tt></a></li>
			</ul>
			<p><b>Prerequisites</b></p>
			<ul>
			    <li><a href="https://www.cosmos.esa.int/web/xmm-newton/sas-thread-startup" target="_parent">SAS Startup Thread</a></li>
			</ul>
			<p><b>Useful Links</b></p>
			<p style="text-align: justify;">Alternatively to following this thread, the pipeline products contain calibrated and concatenated event lists. Both ODFs and pipeline products can be downloaded from the XMM-Newton Science Archive.</p>
			<ul>
                <li><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/pysas/index.html"><tt>pysas</tt></a></li>
                <li><a href="https://www.cosmos.esa.int/documents/332006/918155/sas-startup.ipynb" target="_parent">SAS Startup Thread in Python</a> (<a href="https://www.cosmos.esa.int/web/xmm-newton/sas-thread-startup-in-python" target="_parent">html</a>)</li>
				<li><a href="https://www.cosmos.esa.int/web/xmm-newton/xsa" target="_parent">XMM-Newton Science Archive (XSA)</a></li>
				<li><a href="https://www.cosmos.esa.int/web/xmm-newton/pipeline" target="_blank">PPS Pipeline Products</a></li>
			</ul>
			<p><b><a href="#cav">Caveats</a></b></p>
			<h4>Last Reviewed: <i>31 January 2025, for SAS v22.0</i></h4>
			<h4>Last Updated: <i>15 March 2021</i></h4>
			</td>
		</tr>
	</tbody>
</table>
</center>

<hr />
<h2>Procedure</h2>
<p>Run the EPIC reduction meta-tasks.</p>
<ul>
	<li>For EPIC-MOS:
	<p>&nbsp; <tt>emproc</tt></p>
	</li>&nbsp;
	<li>and for EPIC-pn:
	<p>&nbsp; <tt>epproc</tt></p>
	</li>
</ul>
<p style="text-align: justify;">That's it! The default values of these meta-tasks are appropriate for most practical cases. You may have a look at the next section in this thread to learn how to perform specific reduction sub-tasks using <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/emproc/index.html" target="_parent"><tt>emproc</tt></a> or <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epproc/index.html" target="_parent"><tt>epproc</tt></a>.</p>
<p>The files produced by <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epproc/index.html" target="_parent"><tt>epproc</tt></a> are the following:</p>
<ul>
	<li><tt>????_??????????_AttHk.ds</tt>, the reconstructed attitude file</li>
	<li><tt>????_??????????_EPN_????_01_Badpixels.ds</tt>, one table per reduced CCD containing the bad pixels</li>
	<li><tt>????_??????????_EPN_????_ImagingEvts.ds</tt>, the calibrated and concatenated event list, which shall be used as an input to extract scientific products via <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/evselect/index.html" target="_parent"><tt>evselect</tt></a> or <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/xmmselect/index.html" target="_parent"><tt>xmmselect</tt></a>.</li>
</ul>
<p style="text-align: justify;">The files produced by <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/emproc/index.html" target="_parent"><tt>emproc</tt></a> are conceptually the same. The main difference in the naming convention is that the string <tt>EPN</tt> is replaced by <tt>EMOS1</tt> and <tt>EMOS2</tt> for each EPIC-MOS camera, respectively.</p>
<hr />

<p style="text-align: justify;"><b>In order to run the following blocks, SAS needs to be initialized in the terminal from which the Jupyter nootebook has been opened. This has to be done prior to launching the notebook. ollow the steps provided in the <i>SAS Startup Thread</i> (or <i>SAS Startup Thread in Python</i>).</b></p>

<p style="text-align: justify;">Import the following Python libraries,</p>

In [ ]:
from pysas.wrapper import Wrapper as w
import os
import os.path
from os import path
import subprocess
import numpy as np
import matplotlib.pyplot as plt
from astropy.io import fits
from astropy.table import Table
from matplotlib.colors import LogNorm

<p style="text-align: justify;">Before we start, lets see what se have already defined in terms of SAS variables,</p>

In [ ]:
inargs = []

In [ ]:
t = w('sasver', inargs)

In [ ]:
t.run()

<p style="text-align: justify;">We still need to define the <tt>SAS_ODF</tt> and <tt>SAS_CCF</tt> variables (make sure the SAS_CCFPATH is also defined). Use the SAS task <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/startsas/index.html"><tt>startsas</tt></a> as described in the <i>SAS Startup Thread in Python</i> to download an ODF. For this thread, we will assume that an ODF has already been downloaded. We will use the ODF with id <tt>0104860501</tt> as an example and assume that there is already a directory (<tt>sas_file</tt> in the block below) with an existing <tt>CIF</tt> and Summary File. In the block below introduce the absoute path to the <tt>Working directory</tt> (finished with '/') and the location of the <tt>CIF</tt> and SAS Summary File,</p>

<i><u>Note:</u> the path to the <tt>CIF</tt> and SAS Summary File must be an absolute path begining with '/'.</i>

In [ ]:
work_dir = 'absolute_path_to_wrk_directory'
sas_file = 'absolute_path_to_cifSUMSAS_directory'

In [ ]:
inargs = [f'sas_ccf={sas_file}ccf.cif', f'sas_odf={sas_file}0466_0104860501_SCX00000SUM.SAS', f'workdir={work_dir}']

In [ ]:
w('startsas', inargs).run()

<p style="text-align: justify;">This process should have defined the <tt>SAS_CCF</tt> an <tt>SAS_ODF</tt> variables.</p> 

<p style="text-align: justify;">The following blocks will produce EPIC-pn and EPIC-MOS event files.</p>

<ul>
    <li style="text-align: justify;">Run the SAS command <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epproc/index.html" target="_parent"><tt>epproc</tt></a>. The following blocks are written in such a way that if EPIC-pn event files already exist in the <tt>Working directory</tt>, <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epproc/index.html" target="_parent"><tt>epproc</tt></a> won't run again. To force <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epproc/index.html" target="_parent"><tt>epproc</tt></a> to run, simply delete the corresponding event files.</li>
</ul>

In [ ]:
# SAS Command
cmd    = 'epproc'  # SAS task to be executed

# Arguments of SAS Command
inargs = []        # comma separated arguments for SAS task

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
print("Running epproc ..... \n")

# Check if epproc has already run. If it has, do not run again 
exists = 0
pnevt_list = []
for root, dirs, files in os.walk("."):  
    for filename in files:
        if (filename.find('EPN') != -1) and filename.endswith('ImagingEvts.ds'):
            pnevt_list.append(filename)
            exists = 1        
if exists:    
    print(" > " + str(len(pnevt_list)) + " EPIC-pn event list found. Not running epproc again.\n")
    for x in pnevt_list:
        print("    " + x + "\n")
    print("..... OK")
else:
    w(cmd,inargs).run()      # <<<<< Execute SAS task
    exists = 0
    pnevt_list = []
    for root, dirs, files in os.walk("."):  
        for filename in files:
            if (filename.find('EPN') != -1) and filename.endswith('ImagingEvts.ds'):
                pnevt_list.append(filename)
                exists = 1        
    if exists:    
        print(" > " + str(len(pnevt_list)) + " EPIC-pn event list found after running epproc.\n")
        for x in pnevt_list:
            print("    " + x + "\n")
        print("..... OK")
    else:
        print("Something has gone wrong with epproc. I cant find any event list files after running. \n")

<ul>
    <li style="text-align: justify;">Run the SAS command <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/emproc/index.html" target="_parent"><tt>emproc</tt></a>. The following blocks are written in such a way that if EPIC-MOS event files already exist in the <tt>Working directory</tt>, <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/emproc/index.html" target="_parent"><tt>emproc</tt></a> won't run again. To force <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/emproc/index.html" target="_parent"><tt>emproc</tt></a> to run, simply delete the event files.</li>
</ul>

In [ ]:
# SAS Command
cmd    = 'emproc'  # SAS task to be executed

# Arguments of SAS Command
inargs = []        # comma separated arguments for SAS task

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
print("Running emproc ..... \n")

# Check if emproc has already run. If it has, do not run again 
exists = 0
m1evt_list = []
m2evt_list = []
for root, dirs, files in os.walk("."):  
    for filename in files:
        if (filename.find('EMOS1') != -1) and filename.endswith('ImagingEvts.ds'):
            m1evt_list.append(filename)
            exists = 1 
        if (filename.find('EMOS2') != -1) and filename.endswith('ImagingEvts.ds'):
            m2evt_list.append(filename)
            exists = 1            
if exists:    
    print(" > " + str(len(m1evt_list)) + " EPIC-MOS1 event list found. Not running emproc again.\n")
    for x in m1evt_list:
        print("    " + x + "\n")
    print(" > " + str(len(m2evt_list)) + " EPIC-MOS2 event list found. Not running emproc again.\n")
    for x in m2evt_list:
        print("    " + x + "\n")
    print("..... OK")
else:
    w(cmd,inargs).run()      # <<<<< Execute SAS task
    exists = 0 
    m1evt_list = []
    m2evt_list = []
    for root, dirs, files in os.walk("."):  
        for filename in files:
            if (filename.find('EMOS1') != -1) and filename.endswith('ImagingEvts.ds'):
                m1evt_list.append(filename)
                exists = 1 
            if (filename.find('EMOS2') != -1) and filename.endswith('ImagingEvts.ds'):
                m2evt_list.append(filename)
                exists = 1            
    if exists:    
        print(" > " + str(len(m1evt_list)) + " EPIC-MOS1 event list found. Not running emproc again.\n")
        for x in m1evt_list:
            print("    " + x + "\n")
        print(" > " + str(len(m2evt_list)) + " EPIC-MOS2 event list found. Not running emproc again.\n")
        for x in m2evt_list:
            print("    " + x + "\n")
        print("..... OK")
    else:
        print("Something has gone wrong with emproc. I cant find any event list file. \n")

<ul>
    <li style="text-align: justify;">Visualize the contents of the event files just created. The next blocks can be used to visualize the contents of the newly created event files. A simple selection criteria is impossed for illustration purposes. The thread <i>How to filter EPIC event lists for flaring particle background</i> will show how to use more complex filtering expressions by using the SAS task <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/evselect/index.html" target="_parent"><tt>evselect</tt></a>.</li>
</ul>

In [ ]:
# For display purposes only, define a minimum filtering criteria for EPIC-pn

pn_pattern   = 4        # pattern selection
pn_pi_min    = 300.     # Low energy range eV
pn_pi_max    = 12000.   # High energy range eV
pn_flag      = 0        # FLAG

# For display purposes only, define a minimum filtering criteria for EPIC-MOS

mos_pattern   = 12      # pattern selection
mos_pi_min    = 300.    # Low energy range eV
mos_pi_max    = 20000.  # High energy range eV
mos_flag      = 0       # FLAG

In [ ]:
plt.figure(figsize=(15,20))

pl=1

evts=len(pnevt_list)+len(m1evt_list)+len(m2evt_list)
if len(pnevt_list) >0:
    for x in pnevt_list:  
        hdu_list = fits.open(x, memmap=True)
        evt_data = Table(hdu_list[1].data)
        
        mask = ((evt_data['PATTERN'] <= pn_pattern) &
                (evt_data['FLAG'] == pn_flag) &
                (evt_data['PI'] >= pn_pi_min) &
                (evt_data['PI'] <= pn_pi_max))
        print("Events in event file" + " " + x + ": " + str(len(evt_data)) + "\n")
        print("Events in filtered event file" + " " + x + ": " + str(np.sum(mask)) + "\n")

# Create Events image        

        xmax=np.amax(evt_data['X']) 
        xmin=np.amin(evt_data['X']) 
        xmid=(xmax-xmin)/2.+xmin
        ymax=np.amax(evt_data['Y']) 
        ymin=np.amin(evt_data['Y'])
        xbin_size=80
        ybin_size=80
        NBINS = (int((xmax-xmin)/xbin_size),int((ymax-ymin)/ybin_size))
   
        plt.subplot(evts, 2, pl)

        img_zero_mpl = plt.hist2d(evt_data['X'], evt_data['Y'], NBINS, cmap='GnBu', norm=LogNorm())

        cbar = plt.colorbar(ticks=[10.,100.,1000.])
        cbar.ax.set_yticklabels(['10','100','1000'])
        
        plt.title(x)
        plt.xlabel('x')
        plt.ylabel('y')
   
        pl=pl+1
    
# Create Filtered Events image

        xmax=np.amax(evt_data['X'][mask]) 
        xmin=np.amin(evt_data['X'][mask]) 
        xmid=(xmax-xmin)/2.+xmin
        ymax=np.amax(evt_data['Y'][mask]) 
        ymin=np.amin(evt_data['Y'][mask])
        xbin_size=80
        ybin_size=80
        NBINS = (int((xmax-xmin)/xbin_size),int((ymax-ymin)/ybin_size))
   
        plt.subplot(evts, 2, pl)

        img_zero_mpl = plt.hist2d(evt_data['X'][mask], evt_data['Y'][mask], NBINS, cmap='GnBu', norm=LogNorm())

        cbar = plt.colorbar(ticks=[10.,100.,1000.])
        cbar.ax.set_yticklabels(['10','100','1000'])
        
        plt.title(x)
        plt.xlabel('x')
        plt.ylabel('y')

        txt=("PATTERN <= " + str(pn_pattern) + 
            " : " + str(pn_pi_min) + " <= E(eV) <= " + str(pn_pi_max) + 
            " : " + " FLAG = " + str(pn_flag))
        plt.text(xmid, ymin+0.1*(ymax-ymin), txt, ha='center')
    
        pl=pl+1

        hdu_list.close()
    
if len(m1evt_list) >0:
    for x in m1evt_list:
        hdu_list = fits.open(x, memmap=True)
        evt_data = Table(hdu_list[1].data)

        mask = ((evt_data['PATTERN'] <= mos_pattern) &
                (evt_data['FLAG'] == mos_flag) &
                (evt_data['PI'] >= mos_pi_min) &
                (evt_data['PI'] <= mos_pi_max))
        print("Events in event file" + " " + x + ": " + str(len(evt_data)) + "\n")
        print("Events in filtered event file" + " " + x + ": " + str(np.sum(mask)) + "\n")

# Create Events image            

        xmax=np.amax(evt_data['X']) 
        xmin=np.amin(evt_data['X']) 
        xmid=(xmax-xmin)/2.+xmin
        ymax=np.amax(evt_data['Y']) 
        ymin=np.amin(evt_data['Y'])
        xbin_size=80
        ybin_size=80
        NBINS = (int((xmax-xmin)/xbin_size),int((ymax-ymin)/ybin_size))
   
        plt.subplot(evts, 2, pl)

        img_zero_mpl = plt.hist2d(evt_data['X'], evt_data['Y'], NBINS, cmap='GnBu', norm=LogNorm())

        cbar = plt.colorbar(ticks=[10.,100.,1000.])
        cbar.ax.set_yticklabels(['10','100','1000'])
        
        plt.title(x)
        plt.xlabel('x')
        plt.ylabel('y')
 
        pl=pl+1
    
# Create Filtered Events image

        xmax=np.amax(evt_data['X'][mask]) 
        xmin=np.amin(evt_data['X'][mask]) 
        xmid=(xmax-xmin)/2.+xmin
        ymax=np.amax(evt_data['Y'][mask]) 
        ymin=np.amin(evt_data['Y'][mask])
        xbin_size=80
        ybin_size=80
        NBINS = (int((xmax-xmin)/xbin_size),int((ymax-ymin)/ybin_size))
   
        plt.subplot(evts, 2, pl)

        img_zero_mpl = plt.hist2d(evt_data['X'][mask], evt_data['Y'][mask], NBINS, cmap='GnBu', norm=LogNorm())

        cbar = plt.colorbar(ticks=[10.,100.,1000.])
        cbar.ax.set_yticklabels(['10','100','1000'])
        
        plt.title(x)
        plt.xlabel('x')
        plt.ylabel('y')

        txt=("PATTERN <= " + str(mos_pattern) + 
            " : " + str(mos_pi_min) + " <= E(eV) <= " + str(mos_pi_max) +
            " : " + " FLAG = " + str(mos_flag))
        plt.text(xmid, ymin+0.1*(ymax-ymin), txt, ha='center')
 
        pl=pl+1
    
        hdu_list.close()
    
if len(m2evt_list) >0:
    for x in m2evt_list:
        hdu_list = fits.open(x, memmap=True)
        evt_data = Table(hdu_list[1].data)

        mask = ((evt_data['PATTERN'] <= mos_pattern) &
                (evt_data['FLAG'] == mos_flag) &
                (evt_data['PI'] >= mos_pi_min) &
                (evt_data['PI'] <= mos_pi_max))
        print("Events in event file" + " " + x + ": " + str(len(evt_data)) + "\n")
        print("Events in filtered event file" + " " + x + ": " + str(np.sum(mask)) + "\n")
        
# Create Events image

        xmax=np.amax(evt_data['X']) 
        xmin=np.amin(evt_data['X']) 
        xmid=(xmax-xmin)/2.+xmin
        ymax=np.amax(evt_data['Y']) 
        ymin=np.amin(evt_data['Y'])
        xbin_size=80
        ybin_size=80
        NBINS = (int((xmax-xmin)/xbin_size),int((ymax-ymin)/ybin_size))
   
        plt.subplot(evts, 2, pl)

        img_zero_mpl = plt.hist2d(evt_data['X'], evt_data['Y'], NBINS, cmap='GnBu', norm=LogNorm())

        cbar = plt.colorbar(ticks=[10.,100.,1000.])
        cbar.ax.set_yticklabels(['10','100','1000'])

        plt.title(x)
        plt.xlabel('x')
        plt.ylabel('y')
       
        pl=pl+1
    
# Create Filtered Events image    
       
        xmax=np.amax(evt_data['X'][mask]) 
        xmin=np.amin(evt_data['X'][mask]) 
        xmid=(xmax-xmin)/2.+xmin
        ymax=np.amax(evt_data['Y'][mask]) 
        ymin=np.amin(evt_data['Y'][mask])
        xbin_size=80
        ybin_size=80
        NBINS = (int((xmax-xmin)/xbin_size),int((ymax-ymin)/ybin_size))
   
        plt.subplot(evts, 2, pl)

        img_zero_mpl = plt.hist2d(evt_data['X'][mask], evt_data['Y'][mask], NBINS, cmap='GnBu', norm=LogNorm())

        cbar = plt.colorbar(ticks=[10.,100.,1000.])
        cbar.ax.set_yticklabels(['10','100','1000'])

        plt.title(x)
        plt.xlabel('x')
        plt.ylabel('y')
        
        txt=("PATTERN <= " + str(mos_pattern) + 
            " : " + str(mos_pi_min) + " <= E(eV) <= " + str(mos_pi_max) + 
            " : " + " FLAG = " + str(mos_flag))
        plt.text(xmid, ymin+0.1*(ymax-ymin), txt, ha='center')

        pl=pl+1

        hdu_list.close()
    


<h3>How to accomplish specific reduction tasks<br />
&nbsp;</h3>

<p style="text-align: justify;"><a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/emproc/index.html" target="_parent"><tt>emproc</tt></a> and <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epproc/index.html" target="_parent"><tt>epproc</tt></a> are highly flexible tasks, which allow the user to perform a wide range of customized reduction tasks. Some <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/emproc/index.html" target="_parent"><tt>emproc</tt></a> examples are listed below. The same customized reduction tasks can be performed for the EPIC-pn as well, just by substituting <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/emproc/index.html" target="_parent"><tt>emproc</tt></a> with <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epproc/index.html" target="_parent"><tt>epproc</tt></a> in the commands.</p>

<ul>
	<li>if you want to reduce only one of the cameras (EPIC-MOS1 in the example):<br />
	<br />
	&nbsp;<tt>emproc selectinstruments=yes emos1=yes</tt></li>
</ul>

In [ ]:
# SAS Command
cmd    = "emproc" # SAS task to be executed                  

# Arguments of SAS Command
inargs = ['selectinstruments=yes','emos1=yes']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
w(cmd, inargs).run()

<ul>    
	<li>if you want to reduce only a subsample of exposures:<br />
	<br />
	&nbsp;<tt>emproc withinstexpids=yes instexpids="M1S001 M2S002"</tt></li>
</ul>

In [ ]:
# SAS Command
cmd    = "emproc" # SAS task to be executed                  

# Arguments of SAS Command
inargs = ['withinstexpids=yes','instexpids=M1S001 M2S002']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
w(cmd, inargs).run()

<ul>      
    <li>if you want to reduce data from 1 CCD only (#4 and #5 in the example):<br />
	<br />
	&nbsp;<tt>emproc selectccds=yes ccd4=yes ccd5=yes</tt></li>
</ul>

In [ ]:
# SAS Command
cmd    = "emproc" # SAS task to be executed                  

# Arguments of SAS Command
inargs = ['selectccds=yes','ccd4=yes','ccd5=yes']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
w(cmd, inargs).run()

<ul>      
    <li>if you want to change the reference pointing for the calculation of the sky coordinates to a value of your choice:<br />
	<br />
	&nbsp;<tt>emproc referencepointing=user ra=34.65646 dec=-12.876546</tt></li>
</ul>	

In [ ]:
# SAS Command
cmd    = "emproc" # SAS task to be executed                  

# Arguments of SAS Command
inargs = ['referencepointing=user','ra=34.65646','dec=-12.876546']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
w(cmd, inargs).run()

<p style="text-align: justify;">Please be aware that if you want to supply coordinates for the analysis of the EPIC-MOS Timing mode, the command is slightly different, e.g.:</p>

<p style="text-align: justify;"><tt>&nbsp;&nbsp; emproc withsrccoords=yes srcra=34.65646 srcdec=-12.876546</tt></p>

<ul>      
	<li>if you want to filter the event list events, using an external Good Time Interval (GTI) file (see the corresponding thread on, <i>How to filter event files for flaring particle background by creating a GTI file</i>):<br />
	<br />
	&nbsp;<tt>emproc withgtiset=yes gtiset=mygti.gti filterevents=yes</tt></li>
</ul>

In [ ]:
# SAS Command
cmd    = "emproc" # SAS task to be executed                  

# Arguments of SAS Command
inargs = ['withgtiset=yes','gtiset=mygti.gti','filterevents=yes']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
w(cmd, inargs).run()

<p style="text-align: justify;">Parameters can be combined to accomplish simultaneously two or more of the above tasks during the same run.</p>

<p style="text-align: justify;">The user is referred to the on-line documentation of <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/emproc/index.html" target="_parent"><tt>emproc</tt></a> and <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epproc/index.html" target="_parent"><tt>epproc</tt></a> for a complete list of the available options.</p>

<h3 style="text-align: justify;">Reduction of EPIC-pn Timing Mode exposures<br />
&nbsp;</h3>

<p style="text-align: justify;">Most exposures in EPIC-pn Timing Mode are affected by X-ray Loading (XRL; cf. Sect.3.1 in Guainazzi et al., 2013, <a href="http://xmmweb.esac.esa.int/docs/documents/CAL-TN-0083.pdf">XMM-SOC-CAL-TN-0083</a>). Furthermore, a residual dependence of the energy scale on the total count rate is corrected through the "Rate-Dependent PHA" correction (Guainazzi, 2014, <a href="http://xmmweb.esac.esa.int/docs/documents/CAL-SRN-0312-1-4.pdf">XMM-CCF-REL-312</a>). In order to correct for these effects a set of default calibration settings have been identified. As of SAS v14.0, this is controlled by a single parameter within the tasks <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epproc/index.html" target="_parent"><tt>epproc</tt></a> and <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epchain/index.html" target="_parent"><tt>epchain</tt></a>. This parameter is called <tt>withdefaultcal</tt> and is set to <tt>yes</tt> by default. Setting <tt>withdefaultcal=yes</tt> implies <tt>runepreject=yes withxrlcorrection=yes runepfast=no withrdpha=yes</tt>. So one shall run the EPIC-pn reduction meta-tasks as follows:</p>

<p><tt>&nbsp;&nbsp; epproc </tt></p>

<p>or:</p>

<p><tt>&nbsp;&nbsp; epchain datamode=TIMING </tt></p>

<p>For more information please refer to the documentation of <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epproc/index.html" target="_parent"><tt>epproc</tt></a> and <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epchain/index.html" target="_parent"><tt>epchain</tt></a>.</p>

<h3 style="text-align: justify;">Reduction of EPIC-pn Burst Mode exposures<br />
&nbsp;</h3>

<p style="text-align: justify;">Most exposures in EPIC-pn Burst Mode are affected by X-ray Loading (XRL; cf. Sect.3.1 in Guainazzi et al., 2013, <a href="http://xmmweb.esac.esa.int/docs/documents/CAL-TN-0083.pdf">XMM-SOC-CAL-TN-0083</a>). Furthermore, a residual dependence of the energy scale on the total count rate is corrected through the "Rate-Dependent CTI" correction. In order to correct for these effects a set of default calibration settings have been identified. As of SAS v14.0, this is controlled by a single parameter within the tasks <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epproc/index.html" target="_parent"><tt>epproc</tt></a> and <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epchain/index.html" target="_parent"><tt>epchain</tt></a>. This parameter is called <tt>withdefaultcal</tt> and is set to <tt>yes</tt> by default. Setting <tt>withdefaultcal=yes</tt> implies <tt>runepreject=yes withxrlcorrection=yes runepfast=yes withrdpha=no</tt>. So one shall run the EPIC-pn reduction meta-tasks as follows:</p>

<p><tt>&nbsp;&nbsp; epproc burst=yes</tt></p>

<p>Notice the inclusion of the extra parameter <tt>burst=yes</tt> in the call to <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epproc/index.html" target="_parent"><tt>epproc</tt></a>. The meta-task <a href="https://xmm-tools.cosmos.esa.int/external/sas/current/doc/epchain/index.html" target="_parent"><tt>epchain</tt></a> also needs an extra parameter:</p>

<p><tt>&nbsp;&nbsp; epchain datamode=BURST</tt></p>

In [ ]:
# SAS Command
cmd    = "epchain" # SAS task to be executed                  

# Arguments of SAS Command
inargs = ['datamode=BURST']

print("   SAS command to be executed: "+cmd+", with arguments; \n")
inargs

In [ ]:
w(cmd,inargs).run()

<h3>Should I indeed bother to regenerate my event lists?<br />
&nbsp;</h3>

<p style="text-align: justify;">Concatenated and calibrated EPIC event lists are already available in the <a href="https://www.cosmos.esa.int/web/xmm-newton/pipeline-configurations" target="_blank">PPS Pipeline Products</a>. These are produced with the most updated software and calibrations available at the moment the observation was performed and - normally a couple of weeks later - the ODF are produced. There is therefore no need for you to regenerate the EPIC event lists yourself, unless substantial changes in the software and/or calibration occurred between the time when the <a href="https://www.cosmos.esa.int/web/xmm-newton/pipeline-configurations" target="_blank">Pipeline Products</a> were generated and the moment when you are analyzing the data. Of course, there is no general answer or recipe one can apply to decide if/when this is the case. In order to collect all the available and necessary elements to formulate your judgment, follow these steps:</p>

<ol>
	<li>check in the <a href="https://www.cosmos.esa.int/web/xmm-newton/xsa" target="_parent"> XMM-Newton Science Archive</a> the <a href="https://www.cosmos.esa.int/web/xmm-newton/sas-version-history" target="_parent">SAS version</a> and the date when the <a href="https://www.cosmos.esa.int/web/xmm-newton/current-calibration-files" target="_parent">Calibration Index File</a> was generated to produce the <a href="https://www.cosmos.esa.int/web/xmm-newton/pipeline-configurations" target="_parent">Pipeline Products</a>;</li>
	<li>verify in the <a href="https://www.cosmos.esa.int/web/xmm-newton/sas-release-notes" target="_parent">SAS release notes</a> the software changes between the version employed to produce the <a href="https://www.cosmos.esa.int/web/xmm-newton/pipeline-configurations" target="_parent">Pipeline Products</a> and the <a href="https://www.cosmos.esa.int/web/xmm-newton/sas-version-history" target="_parent">latest SAS version</a>;</li>
	<li>verify in the <a href="https://www.cosmos.esa.int/web/xmm-newton/ccf-release-notes" target="_parent">CCF release notes</a> the changes in the calibration files between the moment when <a href="https://www.cosmos.esa.int/web/xmm-newton/pipeline-configurations" target="_parent">Pipeline Products</a> were generated and the moment your analysis is being performed.</li>
</ol>
&nbsp;

<p>If you feel lost or unsure, and prefer to stay on the safe side, you had probably better regenerate your EPIC calibrated event lists.</p>

<hr />&nbsp;
<center>
<table border="0" style="background-color: #DDDDDD; width: 100%;">
	<tbody>
		<tr>
			<td style="padding: 2px;">
			<p><a name="cav"></a> <b>Caveats</b><br />
			<br />
			None</p>
			</td>
		</tr>
	</tbody>
</table>
</center>
&nbsp;

<hr />
<p>&nbsp;</p>